In [2]:
import json
import pickle
from edgar import *
set_identity('804998502@qq.com@gmail.com')
import os
import openai
from tqdm import tqdm
import pandas as pd
import numpy as np

[11:45:32] INFO     Identity of the Edgar REST client set to [804998502@qq.com@gmail.com]               ]8;id=240480;file:///opt/anaconda3/envs/learn/lib/python3.9/site-packages/edgar/core.py\core.py]8;;\:]8;id=522198;file:///opt/anaconda3/envs/learn/lib/python3.9/site-packages/edgar/core.py#158\158]8;;\

In [3]:
# create a shape (3,2,3) array
a = np.array([[[1,2,3],[4,5,6]],[[7,8,9],[10,11,12]],[[13,14,15],[16,17,18]]])
print(a)

[[[ 1  2  3]
  [ 4  5  6]]

 [[ 7  8  9]
  [10 11 12]]

 [[13 14 15]
  [16 17 18]]]


In [ ]:
# map for country and GICS sector MSCI index ( in bloomberg ticker)
US_GICS_INDEX = {
    'Energy': 'ENRS',
    'Materials': 'MATS',
    'Industrials': 'INDU',
    'Consumer Discretionary': 'CDIS',
    'Consumer Staples': 'CSTP',
    'Health Care': 'HLTH',
    'Financials': 'FINL',
    'Information Technology': 'IT',
    'Communication Services': 'CMCS',
    'Utilities': 'UTIL',
    'Real Estate': 'RLST'
}

In [2]:
import pandas as pd
from openpyxl import Workbook
from openpyxl.styles import Font, Color, PatternFill
from openpyxl.utils.dataframe import dataframe_to_rows

def highlight_sentences(df, text_col, sentence_col, color='FFFF00'):
    wb = Workbook()
    ws = wb.active
    
    # 添加标题行
    ws.append(df.columns.tolist())
    
    for index, row in df.iterrows():
        full_text = row[text_col]
        key_sentence = row[sentence_col]
        start = full_text.find(key_sentence)
        end = start + len(key_sentence)
        
        # 将文本分为三部分：前、关键句子、后
        parts = [full_text[:start], full_text[start:end], full_text[end:]]
        
        # 插入行
        row_to_insert = [parts[0], key_sentence, parts[2], *row[df.columns.difference([text_col, sentence_col])]]
        ws.append(row_to_insert)
        
        # 高亮关键句子
        cell = ws.cell(row=index + 2, column=2)  # 因为有标题行和从0开始的index
        cell.fill = PatternFill(start_color=color, end_color=color, fill_type="solid")
    
    return wb

# 示例DataFrame
data = {
    'text': ["这是一段很长的文本，其中有一个很重要的关键句子。", "第二段文本，包含另一个关键句子。"],
    'key_sentence': ["一个很重要的关键句子", "包含另一个关键句子"]
}
df = pd.DataFrame(data)

# 应用高亮并保存到Excel
wb = highlight_sentences(df, 'text', 'key_sentence')
wb.save('highlighted_text.xlsx')


In [2]:
def find_plan_date(content_input):
    # optional; defaults to `os.environ['OPENAI_API_KEY']`
    openai.api_key = "sk-tDimWbhxdM5vMsjG55A9B843894441228c4fB89177C32a1e"

    # all client options can be configured just like the `OpenAI` instantiation counterpart
    openai.base_url = "https://free.gpt.ge/v1/"
    openai.default_headers = {"x-foo": "true"}

    completion = openai.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {
                "role": "user",
                "content": content_input,
            },
        ],
    )
    return completion.choices[0].message.content

In [3]:
year = 2023

with open(f'freeze_collection_{year}.pkl', 'rb') as f:
    freeze_collection = pickle.load(f)

# find the key which is not none
freeze_collection = {k: v for k, v in freeze_collection.items() if v is not None}


In [14]:
# value
freeze_collection

{'0001493152-23-046365': {'query': '\\b(?:freeze|froze|frozen|freezing|close|closed|discontinue|discontinued|terminate|terminated|renegotiate|renegotiated)\\b(?:\\W+\\w+){0,20}?\\W+\\b(?:defined benefit|pension plan|retirement|postretirement|postemployment|pension|benefit)\\b|\\b(?:defined benefit|pension plan|retirement|postretirement|postemployment|pension|benefit)\\b(?:\\W+\\w+){0,20}?\\W+\\b(?:freeze|froze|frozen|freezing|close|closed|discontinue|discontinued|terminate|terminated|renegotiate|renegotiated)\\b',
  'sections': [{'loc': 323,
    'doc': '| For the year ended | \n | September 30, 2023 | | | September 30, 2022 | \nRevenues | $ | 59,368,562 | | | $ | 45,026,780 | \nCost of revenues | | 33,682,736 | | | | 28,460,852 | \nGross profit | | 25,685,826 | | | | 16,565,928 | \nOperating expenses | | | | | | | \nGeneral and administrative | | 23,929,340 | | | | 22,934,555 | \nResearch and development | | 3,267,994 | | | | 4,444,488 | \nGoodwill impairment | | - | | | | 3,316,000 | 

In [12]:
for number, i in enumerate(freeze_collection['0001493152-23-046365']['sections']):
    print(number, i)

0 {'loc': 323, 'doc': '| For the year ended | \n | September 30, 2023 | | | September 30, 2022 | \nRevenues | $ | 59,368,562 | | | $ | 45,026,780 | \nCost of revenues | | 33,682,736 | | | | 28,460,852 | \nGross profit | | 25,685,826 | | | | 16,565,928 | \nOperating expenses | | | | | | | \nGeneral and administrative | | 23,929,340 | | | | 22,934,555 | \nResearch and development | | 3,267,994 | | | | 4,444,488 | \nGoodwill impairment | | - | | | | 3,316,000 | \nTotal operating expenses | | 27,197,334 | | | | 30,695,043 | \nOperating loss | | (1,511,508 | ) | | | (14,129,115 | )\nOther (expense)/income | | | | | | | \nOther income, net | | 476,693 | | | | 7,180,738 | \nInterest expense | | (4,966,298 | ) | | | (3,878,703 | )\nTotal other (expense)/income, net | | (4,489,605 | ) | | | 3,302,035 | \nNet loss before income taxes | | (6,001,113 | ) | | | (10,827,080 | )\nIncome tax (expense)/benefit | | (394,272 | ) | | | 209,345 | \nLoss from Continuing operations | | (6,395,385 | ) | | | (

In [17]:
freeze_date_collection = {}

for key, value in tqdm(freeze_collection.items()):

    content_input= 'According to the following document, is there any plan\
        that was frozen or terminated? if yes, please provide the name of the plan and the date of the freeze or termination \
            (the date should be in the form of yyyy/mm/dd, and there should be a [,] betweem output plan and date).\
            Please make sure your answer is in the form of (plan name, date of freeze or termination). \
                If the document does not mention any plans that were frozen or terminated, \please answer (None) \
                    The document includes several sections, each sections are part of the same financial statement\
                        , please go through all sections and give the most updated date and plan needed:'

    sections_content = ''

    for n, section in enumerate(value['sections']):
        sections_content += f"[Section {n}: {section['doc']}]"

    content_input += sections_content


    response = find_plan_date(content_input)

    freeze_date_collection[key] = response

    if response != '(None)':
        print(key, response)
        break
    


<>:5: SyntaxWarning: invalid escape sequence '\p'
<>:5: SyntaxWarning: invalid escape sequence '\p'
C:\Users\TJR\AppData\Local\Temp\ipykernel_35384\1433096768.py:5: SyntaxWarning: invalid escape sequence '\p'
  content_input= 'According to the following document, is there any plan\
  0%|          | 1/715 [00:01<22:31,  1.89s/it]

0000808326-23-000031 (Pension Plan, 2022/07/01)


In [13]:
results = pd.DataFrame(freeze_date_collection.items(), columns=['key', 'value'])
results.rename(columns={'key': 'accession_number'}, inplace=True)

NameError: name 'freeze_date_collection' is not defined

In [32]:
filings = get_filings(2023, form=['10-K', '10-Q'])
df_filings = filings.to_pandas()
df_filings

form                                    company      cik filing_date  \
0        10-K  Atmos Energy Kansas Securitization I, LLC  1967097  2023-12-29   
1        10-K               Citius Pharmaceuticals, Inc.  1506251  2023-12-29   
2        10-K                  FLANIGANS ENTERPRISES INC    12040  2023-12-29   
3        10-K                    GLOBAL TECHNOLOGIES LTD   932021  2023-12-29   
4        10-K                                MariaDB plc  1929589  2023-12-29   
...       ...                                        ...      ...         ...   
27829  10-K/A        Liberty Resources Acquisition Corp.  1880151  2023-01-03   
27830    10-Q                           Blubuzzard, Inc.  1765826  2023-01-03   
27831    10-Q                            IA Energy Corp.  1673431  2023-01-03   
27832    10-Q                SMART Global Holdings, Inc.  1616533  2023-01-03   
27833    10-Q                                 SRAX, Inc.  1538217  2023-01-03   

           accession_number  
0      0001967097-23-000004  
1      0001213900-23-099889  
2      0001174947-23-001489  
3      0001493152-23-046428  
4      0001929589-23-000010  
...                     ...  
27829  0001104659-22-131423  
27830  0001599916-23-000002  
27831  0001096906-23-000005  
27832  0001628280-23-000100  
27833  0001493152-22-037214  

[27834 rows x 5 columns]

In [33]:
df_filings['accession_number'] = df_filings['accession_number'].astype(str)
results['accession_number'] = results['accession_number'].astype(str)

In [36]:
# use the accession_number to map cik, company, and filing_date from df_filings to results
results = pd.merge(results, df_filings, on='accession_number', how='left')
results



accession_number                                          value  \
0    0001493152-23-046365                                         (None)   
1    0000808326-23-000031                     (Pension Plan, 2022/07/01)   
2    0001552781-23-000490                                         (None)   
3    0001645590-23-000117                                         (None)   
4    0001342423-23-000037  (Defined Benefit Retirement Plan, 2021/12/31)   
..                    ...                                            ...   
757  0001084765-23-000005                                         (None)   
758  0000950170-23-000211                                         (None)   
759  0000950170-23-000260                                         (None)   
760  0001618921-23-000005               (Boots Pension Plan, 2010/07/01)   
761  0000940944-23-000004                                         (None)   

     form                           company      cik filing_date  
0    10-K                       CEMTREX INC  1435064  2023-12-28  
1    10-K                       EMCORE CORP   808326  2023-12-27  
2    10-Q                  Bancorp 34, Inc.  1668340  2023-12-27  
3    10-K     Hewlett Packard Enterprise Co  1645590  2023-12-22  
4    10-K                      Limoneira CO  1342423  2023-12-21  
..    ...                               ...      ...         ...  
757  10-Q        RESOURCES CONNECTION, INC.  1084765  2023-01-05  
758  10-Q  SCHNITZER STEEL INDUSTRIES, INC.   912603  2023-01-05  
759  10-Q                     UNIFIRST CORP   717954  2023-01-05  
760  10-Q    Walgreens Boots Alliance, Inc.  1618921  2023-01-05  
761  10-Q            DARDEN RESTAURANTS INC   940944  2023-01-04  

[762 rows x 6 columns]

In [37]:
results.to_csv(f'freeze_date_collection_{year}.csv', index=False)